In [1]:
import numpy as np
import sys
import copy
import pandas as pd
import os
import argparse
from os.path import join
import matplotlib.pyplot as plt 
from matplotlib import cm
import datetime
import itertools
import openpyxl
import statistics
import seaborn as sns

In [2]:
def file_convert(file_name):
    correct_name = file_name.replace(chr(92),'/')
    return correct_name

In [10]:
#import data
input_data = r"C:\Users\81906\Desktop\研究関連\NIMS_experiments\0710_sporomusa\0710_sporomusa_honjo.csv"
input_data = file_convert(input_data)
#import sample_sheet
input_sheet = r"C:\Users\81906\Desktop\研究関連\NIMS_experiments\0710_sporomusa\230710_takee2.xlsx"
input_sheet = file_convert(input_sheet)

In [11]:
# data selecting
data_start = 1
def import_data(input_data):
    #data selection
    global data_start
    data = pd.read_csv(input_data, header = None, index_col = None, sep = ",")
    if data.iloc[0,1]=='start':
        data_start=data_start+1
    selected = data.iloc[:,data_start:]
    
    #time calculation
    dt1=data[0][0]
    dt2=data[0][1]
    tdatetime1 = datetime.datetime.strptime(dt1, '%Y/%m/%d %H:%M:%S')
    tdatetime2 = datetime.datetime.strptime(dt2, '%Y/%m/%d %H:%M:%S')
    tdelta=tdatetime2-tdatetime1
    
    return tdelta,data_start,selected

tdelta,data_start,selected = import_data(input_data)

In [12]:
#time conversion

#aerobic
timescale="hour"
#timescale="min"

#time = selected.index.values
time = selected.index.values
if timescale == "hour":
    xdata = (time/3600)*tdelta.seconds
elif timescale == "min":
    xdata = (time/60)*tdelta.seconds

In [13]:
#data information from sample_sheet
sample_s = pd.read_excel(input_sheet, header = None, index_col = None)

#name information
med_name = sample_s.iloc[2,2:14]
med_name=med_name.reset_index(drop=True)

#data selection
sample_s = sample_s.iloc[4:12,2:14]
sample_s = sample_s.values
sample_s = np.ravel(sample_s)
sample_s = np.array([x for x in sample_s])
CA_data=selected.iloc[:,::data_start]
#CA_data=selected

In [ ]:
sample_s
CA_data

In [14]:
#sort
sample_s_sort=np.sort(sample_s,kind="mergesort")
sample_s_sort_id=np.argsort(sample_s,kind="mergesort")
sample_CA_sort=selected.iloc[:,sample_s_sort_id*data_start]

In [15]:
#All wells in 96 position

#graph properties
fig = plt.figure(figsize=(24, 18),dpi = 500)
plt.subplots_adjust(wspace=0.7, hspace=0.7)

#drawing
for i in range (int(CA_data.shape[1])):
    plt.subplot(8,12,i+1)
    ydata = CA_data.iloc[:,i]
    ydata = ydata*10**9
    plt.title('['+chr(i//12+65)+str(i%12+1)+']'+'\n'+str(sample_s[i]), fontsize=12)
    plt.plot(xdata,ydata,linewidth=4,color='tab:red')
    #plt.ylim(0, 200)
#plt.savefig(file_convert(r"C:\Users\81906\Desktop\NIMS_experiments\0606_experiment\230606substrate_result"),facecolor="white",bbox_inches='tight')
plt.show()


In [16]:
#All wells in one figure

#graph properties
fig = plt.figure(figsize=(24, 18),dpi = 500)
plt.subplots_adjust(wspace=0.7, hspace=0.7)

CA_data=sample_CA_sort

#drawing
for i in range (int(CA_data.shape[1])):
    ydata = CA_data.iloc[:,i]
    #ydata = CA_data.iloc[:,i//8+(i%8)*12]
    ydata = ydata*10**9
    plt.xlabel('Time (hour)' ,fontsize = 20)
    plt.ylabel('Current (nA)',fontsize = 20)
    #if CA_data.iloc[2*60*60,i//8+(i%8)*12] > 800*10**(-9):
        #color='blue'
    #else: 
        #color='red'     
    plt.plot(xdata,ydata,linewidth=0.5, label='['+chr(i//12+65)+str(i%12+1)+']')
    legend = plt.legend(bbox_to_anchor=(0.5, 1.00), loc="lower center", borderaxespad=0, fontsize=15, ncol = int(CA_data.shape[1]/8))
plt.tick_params(labelsize=22)
plt.ylim(0, 2000)
plt.xlim(0,50)
#plt.savefig('/Users/takashi/Desktop/test',facecolor="white",bbox_inches='tight')
plt.show()

In [17]:
#sample replication
sample_rep=[]
def sample_rep_comb(data):
    global sample_rep
    for i in range(len(data)):
        test=np.where(data==data[i])
        if i == 0:
            sample_rep.append(test)
        else:
            try:
                if(sample_rep[len(sample_rep)-1][0] == test[0]).all():
                    continue
                else:
                    sample_rep.append(test)
            except:
                sample_rep.append(test)
    return sample_rep

sample_rep = sample_rep_comb(sample_s_sort)

#the number of rep
rep_num=[]
for i in range(len(sample_rep)):
    rep_num.append(len(sample_rep[i][0]))

C:\Users\81906\AppData\Local\Temp\ipykernel_7032\1274166495.py:11: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  if(sample_rep[len(sample_rep)-1][0] == test[0]).all():


In [18]:
#compress_sample
comp_sample=[]
t=0
for i in range(len(rep_num)):
    comp_sample.append(sample_s_sort[t])
    t=t+rep_num[i]

In [19]:
#corration of error peak
def remove_error_peak(run,time_span,current):
    if run == 1:
        #default
        CA_data=sample_CA_sort        
        CA_diff=CA_data.diff(time_span)
        CA_data_NaN=CA_data.where(np.abs(CA_diff)<current, np.nan)
        CA_data_corr=CA_data_NaN.astype(float).interpolate()
        #window=60
        #CA_data_corr=CA_data_corr.rolling(window, center=True).mean()
    elif run == 0:
        CA_data_corr=sample_CA_sort
    return CA_data_corr

#(t)分前よりも(current)A変動
peak_remove = 0 #No=0, run=1
CA_error_peak_removed=remove_error_peak(peak_remove,1,1*-6)


In [20]:
#baseline substraction
#全体のminを引く
def baseline_substraction(run):
    CA_data_bs = pd.DataFrame(index=[])
    if run == 1:
        CA_first=CA_error_peak_removed
        CA_first=CA_first.min()
        CA_first=CA_first.reset_index()
        for i in range (CA_error_peak_removed.shape[1]):
            CA_data_bs.loc[:,i]=CA_error_peak_removed.iloc[:,i]-CA_first.loc[i].iloc[-1]
    elif run == 0:
        CA_data_bs=CA_error_peak_removed
    return CA_data_bs


Base_sub = 0 #0 = No,1=run
CA_data_bs=baseline_substraction(Base_sub)

In [21]:
#Average with Standard Deviation

replicate = 4
n_comb = 3


data_CA=CA_data_bs

average = pd.DataFrame(columns=[int(x) for x in np.linspace(0,len(sample_rep)-1,len(sample_rep))])
SD_check=[]
SD_comb=[]
for s in range(average.shape[1]):
    f_col = s*replicate
    e_col = f_col+replicate
    sample_judge=data_CA.iloc[:,f_col:e_col]

    #組み合わせを取得
    combination_array=[]
    for index in itertools.combinations(sample_judge.columns, n_comb):
        combination_array.append(index)
    comb=np.array(combination_array)
    SD_comb.append(comb)

    SD_min_all=[]
    for t in range (0,int(sample_judge.shape[0]/60/60),1):
        SD_array=[]
        for current in comb:
            SD_array.append(np.std(sample_judge.iloc[t*60*60,current%replicate]))
            SD_min=SD_array.index(min(SD_array))
        SD_min_all.append(SD_min)
    SD_check.append(SD_min_all)
    #print(SD_array)
    mode = statistics.mode(SD_min_all)
    sample_i= data_CA.iloc[:,comb[mode]]
    average.loc[:,s] = np.mean(sample_i,axis=1)

#smoothing range
window=1*60*60

CA_data_final=average.rolling(window, center=True).mean()

StatisticsError: no mode for empty data

In [ ]:
print("SD_min_all:", SD_min_all)
print("min value:", min(SD_min_all))
print("max value:", max(SD_min_all))
print("mode:", statistics.mode(SD_min_all))
print(mode)

In [ ]:
#Average
def average(data):
    CA_average = pd.DataFrame(columns=comp_sample)
    for s in range(len(sample_rep)):
        CA_average.iloc[:,s] = np.mean(data.iloc[:,sample_rep[s][0]],axis=1)
    return CA_average

CA_data_final=average(CA_data_bs)

#smoothing range
window=1*60
CA_data_final=CA_data_final.rolling(window, center=True).mean()

In [ ]:
CA_data_final.iloc[100:500,5]

In [ ]:
#All CA data (Average)

#graph proerties
fig = plt.figure(dpi=500)
plt.rcParams['font.family'] = 'Arial'
sns.set()
sns.set_style('ticks')
sns.set_palette('hls',CA_data_final.shape[1])
ax = fig.add_subplot(111)
plt.xlabel('Time (hour)' ,fontsize = 15)
plt.ylabel('Current (nA)',fontsize = 15)

#drawing
t=0
for i in range(int(CA_data_final.shape[1])):
    #if i in [0,1,2,3]:
    ydata = CA_data_final.iloc[:,i]
    ydata = ydata*10**9
    plt.plot(xdata,ydata,linewidth=0.5, label=sample_s_sort[t])
    t=t+rep_num[i]
    legend = plt.legend(bbox_to_anchor=(0.5, 1.00), loc="lower center", borderaxespad=0, fontsize=8, ncol = 4)
plt.ylim(0, 2000)
plt.tick_params(labelsize=12)
#plt.savefig('/Users/takashi/Desktop/med_ecoli_1nA+1sec_min_1h_rolling',facecolor="white",bbox_inches='tight')
plt.show

In [ ]:
#current
CA_data_final_current=CA_data_final.iloc[1*60:10*60,:].max()

In [ ]:
CA_data_final_current

In [ ]:
#slope
CA_data_final_slope=CA_data_final.diff()
slope_max=CA_data_final_slope.iloc[1*60:10*60,:].max()

In [ ]:
pd.set_option('display.max_rows', None)
slope_max

In [ ]:
#classification
if "CA_data_1" in locals():
    del CA_data_1

if "CA_data_2" in locals():
    del CA_data_2

for x in range(CA_data_bs.shape[1]):
    if CA_data_bs.iloc[2*60*60,x] > 800*10**(-9):
        #if x != 56:
        if "CA_data_1" not in locals():
            CA_data_1=CA_data_bs.iloc[:,x]
        else:
            CA_data_1 = pd.concat([CA_data_1, CA_data_bs.iloc[:,x]], axis = 1)
    else:
        if "CA_data_2" not in locals():
            CA_data_2=CA_data_bs.iloc[:,x]
        else:
            CA_data_2 = pd.concat([CA_data_2, CA_data_bs.iloc[:,x]], axis = 1)

In [ ]:
#All wells in one figure

#graph properties
fig = plt.figure(figsize=(24, 18),dpi = 500)
plt.subplots_adjust(wspace=0.7, hspace=0.7)

data=CA_data_1_slope

#drawing
for i in range (int(data.shape[1])):
    ydata = data.iloc[:,i]
    ydata = ydata*10**9
    plt.xlabel('Time (hour)' ,fontsize = 20)
    plt.ylabel('Slope (nA/s)',fontsize = 20)
    plt.plot(xdata,ydata,linewidth=0.5, label=sample_s[i])
    legend = plt.legend(bbox_to_anchor=(0.5, 1.00), loc="lower center", borderaxespad=0, fontsize=15, ncol = int(CA_data.shape[1]/12))
plt.tick_params(labelsize=22)
#plt.ylim(0, 1500)
plt.savefig('/Users/takashi/Desktop/well_error_blue_slope',facecolor="white",bbox_inches='tight')
plt.show()

In [ ]:
#slope
CA_data_1_slope=CA_data_1.diff()
CA_data_2_slope=CA_data_2.diff()

#slope max
#slope_max1=CA_data_1_slope.iloc[1*60*60:10*60*60,:].max()
slope_max1=CA_data_1_slope.max()
slope_max2=CA_data_2_slope.iloc[1*60*60:10*60*60,:].max()
#slope_max_time=CA_slope.iloc[1*60*60:10*60*60,:].astype(float).idx

In [ ]:
pd.set_option('display.max_rows', None)
slope_max1

In [ ]:
#class1
slope_max_ave1=np.average(slope_max1)
#slope_max_max1=slope_max1.max()
#slope_max_min1=slope_max1.min()

In [ ]:
slope_max_ave1

In [ ]:
np.std(slope_max1,ddof=1)

In [ ]:
np.std(slope_max1,ddof=1)/slope_max_ave1

In [ ]:
#average
#3.164552768738598e-11→3.085882828681274e-11

#std
#7.373630864365914e-12→3.953747388713915e-12

In [ ]:
#average
#9.70638213501103e-11→9.701896761242688e-11

#std
#7.373630864365914e-12→5.6064920628095944e-12

#error
#0.05741046211099879→0.057787587322166836

In [ ]:
#class2
slope_max_ave2=np.average(slope_max2)
#slope_max_max1=slope_max1.max()
#slope_max_min1=slope_max1.min()
np.std(slope_max2,ddof=1)/slope_max_ave2

In [ ]:
np.std(slope_max2,ddof=1)

In [ ]:
abs((slope_max_ave1-slope_max_max1)/slope_max_ave1)*100

In [ ]:
abs((slope_max_ave1-slope_max_min1)/slope_max_ave1)*100

In [ ]:
#class2
slope_max_ave2=np.average(slope_max2)
slope_max_max2=slope_max2.max()
slope_max_min2=slope_max2.min()

In [ ]:
abs((slope_max_ave2-slope_max_max2)/slope_max_ave2)*100

In [ ]:
abs((slope_max_ave2-slope_max_min2)/slope_max_ave2)*100

In [ ]:
#Average220803_thio_conc
def average(data):
    CA_average = pd.DataFrame(columns=comp_sample)
    for s in range(len(sample_rep)):
        sample_s_sort2=np.sort(data.iloc[:,sample_rep[s][0]].max(),kind="mergesort")
        sample_s_sort_id2=np.argsort(data.iloc[:,sample_rep[s][0]].max(),kind="mergesort")
        CA_average.iloc[:,s]=np.mean(CA_data_bs.loc[:,sample_s_sort_id2.index[np.array(sample_s_sort_id2[-2:])]],axis=1)
    return CA_average
CA_data_final=average(CA_data_bs)

In [ ]:
CA_data_final.max()

In [ ]:
##All wells in one sample with average##

#def allwell_average(data_name, file_name):
#graph proerties

data_name=CA_data_bs
replicate=96

fig = plt.figure(figsize=(60, 200))
plt.rcParams['font.family'] = 'Arial'
sns.set()
sns.set_style('ticks')
sns.set_palette('hls',CA_data_final.shape[1])
ax = fig.add_subplot(111)

#drawing
t=0
for i in range (len(rep_num)):
    for t in range(i*replicate,(i+1)*replicate):
        plt.subplot(int(data_name.shape[1]/3),3,i+1)
        plt.xlabel('Time (hour)' ,fontsize = 25)
        plt.xticks(fontsize=20)
        plt.ylabel('Current (nA)',fontsize = 25)
        plt.yticks(fontsize=20)
        ydata = np.std(data_name.iloc[:,t])
        ydata = ydata*10**9
        plt.plot(xdata,ydata,linewidth=1,color='gray')
    #drawing with average
    ydata_a = CA_data_final.iloc[:,i]
    ydata_a = ydata_a*10**9
    plt.plot(xdata,ydata_a,linewidth=1, color='red')
    plt.subplots_adjust(wspace=0.3, hspace=0.5)
    plt.title(sample_s_sort[t],fontsize=30)
    t=t+rep_num[i]
    plt.ylim(0, 1500)
#plt.ioff()
#plt.savefig(dirname+bac_name+date+'replicate+average'+file_name,bbox_inches='tight')
#plt.savefig('ecoli-aerobic-220619_average_EP_BS_SD8of12'+file_name,bbox_inches='tight')
#plt.close(fig)
plt.show()

#allwell_average(CA_data, 'rawdata')
#allwell_average(CA_data_bs, 'correction')

In [ ]:
#slope
CA_slope=CA_data_bs.diff()

#slope max
slope_max=CA_slope.iloc[1*60*60:10*60*60,:].max()
#slope_max_time=CA_slope.iloc[1*60*60:10*60*60,:].astype(float).idx

In [ ]:
slope_max
slope_max_ave=np.average(slope_max)
slope_max_max=slope_max.max()
slope_max_min=slope_max.min()

In [ ]:
abs((slope_max_ave-slope_max_max)/slope_max_ave)*100

In [ ]:
abs((slope_max_ave-slope_max_min)/slope_max_ave)*100

In [ ]:
slope_max_ave

In [ ]:
slope_max_min

In [ ]:
(slope_max_ave-slope_max_max)/slope_max_ave